In [1]:
from DPOD.datasets.linemod.models_handler import read_obj_file
import numpy as np
from glob import glob

# Core functions

In [2]:
def process_face(vertices, face):
    v_face = vertices[face, :]
    h_diff = v_face[:, 0].max() - v_face[:, 0].min()
    w_diff = v_face[:, 1].max() - v_face[:, 1].min()
    z_diff = v_face[:, 2].max() - v_face[:, 2].min()
    diff = max(h_diff, w_diff, z_diff)
    if -1 in face:
        print("elo")
    if diff > 0.001:
        mids = np.stack([v_face[[2, 1]].mean(axis=0), 
                         v_face[[0, 2]].mean(axis=0), 
                         v_face[[0, 1]].mean(axis=0)])
        mids_ids = [len(vertices) + i for i in range(3)]
        vertices = np.concatenate([vertices, mids])
        faces = []
        for i in range(3):
            vertices, new_faces = process_face(vertices, np.array([face[i], mids_ids[(i+1)%3], mids_ids[(i+2)%3]]))
            faces += new_faces
        vertices, new_faces = process_face(vertices, mids_ids)
        faces += new_faces

    else:
        faces = [face]
    
    return vertices, faces

In [3]:
def save_obj_file(filename, ver, facs):
    with open(filename, "w") as file:
        for v in ver:
            file.write(f"v {v[0]} {v[1]} {v[2]}\n")
            
        for f in facs:
            file.write(f"f {f[0]} {f[1]} {f[2]}\n")

# Testing

In [4]:
ver, facs = read_obj_file("models_small/Duck/007_small.obj")

In [5]:
faces = []
for face in facs:
    ver, new_faces = process_face(ver, face)
    faces += new_faces
print(ver.shape, np.array(faces).shape)
print(np.array(faces).min(), np.array(faces).max())

(171790, 3) (172288, 3)
0 171789


In [6]:
len(ver)

171790

In [7]:
save_obj_file("test.obj", ver, facs)

# Generate big models

In [8]:
import os
from tqdm.notebook import tqdm


for model_dir in tqdm(glob(f'models_small/*')):
    model_name = os.path.split(model_dir)[1]
    if 'Holepuncher' in model_dir:
        continue
    model_filepath = glob(f'{model_dir}/*.obj')[0]
    ver, facs = read_obj_file(model_filepath)
    faces = []
    for face in facs:
        ver, new_faces = process_face(ver, face)
        faces += new_faces
    os.makedirs(f"models_big/{model_dir.split('/')[1]}", exist_ok=True)
    save_obj_file(f"models_big/{model_dir.split('/')[1]}/001.obj", ver, np.array(faces) + 1)

# Generate reversed_mapping using new approach

In [1]:
import os
from tqdm.notebook import tqdm
import numpy as np
from DPOD.datasets.linemod.models_handler import ModelsHandler
from DPOD.datasets.linemod.models_handler import get_reversed_mapping
from glob import glob


mh = ModelsHandler()
for model_dir in glob(f'models_small/*'):
    model_name = os.path.split(model_dir)[1]
    if 'Holepuncher' in model_dir:
        continue
    mapping = get_reversed_mapping(mh, model_name)
    
    os.makedirs(f"models_big/{model_name}", exist_ok=True)
    np.save(f"models_big/{model_name}/mapping.npy", mapping)
    print(f"Done {model_name}")

  0%|          | 211/65025 [00:00<00:36, 1779.94it/s]

{'Ape': 1, 'Can': 2, 'Cat': 3, 'Driller': 4, 'Duck': 5, 'Eggbox': 6, 'Glue': 7}


  0%|          | 167/65025 [00:00<00:57, 1134.68it/s]

Done Ape



  6%|▌         | 3916/65025 [00:05<08:27, 120.47it/s]


...

 93%|█████████▎| 60252/65025 [02:48<00:45, 106.03it/s]





 93%|█████████▎| 60259/65025 [02:48<00:44, 106.03it/s]





 93%|█████████▎| 60282/65025 [02:48<00:45, 103.21it/s]





 93%|█████████▎| 60282/65025 [02:48<00:45, 103.21it/s]





 93%|█████████▎| 60290/65025 [02:48<00:45, 103.21it/s]





 93%|█████████▎| 60292/65025 [02:48<00:45, 103.21it/s]





 93%|█████████▎| 60306/65025 [02:48<00:45, 103.21it/s]





 93%|█████████▎| 60311/65025 [02:48<00:45, 103.21it/s]





 93%|█████████▎| 60328/65025 [02:48<00:45, 102.71it/s]





 93%|█████████▎| 60333/65025 [02:48<00:45, 102.71it/s]





 93%|█████████▎| 60342/65025 [02:48<00:49, 94.94it/s] 





 93%|█████████▎| 60347/65025 [02:48<00:49, 94.94it/s]





 93%|█████████▎| 60353/65025 [02:48<00:49, 94.94it/s]





 93%|█████████▎| 60360/65025 [02:48<00:48, 95.31it/s]





 93%|█████████▎| 60366/65025 [02:48<00:48, 95.31it/s]





 93%|█████████▎| 60373/65025 [02:48<00:48, 95.31it/s]





 93%|█████████▎| 60381/65025 [02:48<00:48, 95

 96%|█████████▌| 62225/65025 [02:53<00:20, 138.09it/s]





 96%|█████████▌| 62232/65025 [02:53<00:20, 138.09it/s]





 96%|█████████▌| 62244/65025 [02:53<00:20, 138.09it/s]





 96%|█████████▌| 62277/65025 [02:53<00:20, 132.19it/s]





 96%|█████████▌| 62279/65025 [02:53<00:20, 132.48it/s]





 96%|█████████▌| 62279/65025 [02:53<00:20, 132.48it/s]





 96%|█████████▌| 62283/65025 [02:53<00:20, 132.48it/s]





 96%|█████████▌| 62288/65025 [02:53<00:20, 132.48it/s]





 96%|█████████▌| 62295/65025 [02:53<00:20, 132.48it/s]





 96%|█████████▌| 62301/65025 [02:53<00:20, 132.48it/s]





 96%|█████████▌| 62307/65025 [02:53<00:20, 132.48it/s]





 96%|█████████▌| 62334/65025 [02:53<00:20, 131.42it/s]





 96%|█████████▌| 62337/65025 [02:53<00:20, 132.85it/s]





 96%|█████████▌| 62338/65025 [02:53<00:20, 132.85it/s]





 96%|█████████▌| 62352/65025 [02:53<00:20, 132.85it/s]





 96%|█████████▌| 62355/65025 [02:53<00:20, 132.85it/s]





 96%|█████████▌| 62361/65025 [02:53<00:2

 99%|█████████▊| 64105/65025 [02:58<00:07, 124.47it/s]





 99%|█████████▊| 64123/65025 [02:58<00:07, 128.10it/s]





 99%|█████████▊| 64128/65025 [02:58<00:06, 133.23it/s]





 99%|█████████▊| 64129/65025 [02:58<00:06, 133.23it/s]





 99%|█████████▊| 64136/65025 [02:58<00:06, 133.23it/s]





 99%|█████████▊| 64145/65025 [02:58<00:06, 133.23it/s]





 99%|█████████▊| 64150/65025 [02:58<00:06, 133.23it/s]





 99%|█████████▊| 64171/65025 [02:58<00:06, 135.60it/s]





 99%|█████████▊| 64180/65025 [02:58<00:06, 135.60it/s]





 99%|█████████▊| 64204/65025 [02:58<00:05, 137.93it/s]





 99%|█████████▊| 64209/65025 [02:58<00:05, 150.14it/s]





 99%|█████████▊| 64212/65025 [02:58<00:05, 150.14it/s]





 99%|█████████▉| 64213/65025 [02:58<00:05, 150.14it/s]





 99%|█████████▉| 64226/65025 [02:58<00:05, 150.14it/s]





 99%|█████████▉| 64233/65025 [02:58<00:05, 150.14it/s]





 99%|█████████▉| 64253/65025 [02:58<00:05, 149.84it/s]





 99%|█████████▉| 64255/65025 [02:58<00:0

Done Driller








100%|██████████| 65025/65025 [03:17<00:00, 309.81it/s]